<!-- LTeX: language=fr -->

Cours 10 : Générer du HTML
==========================

**Loïc Grobol** [<lgrobol@parisnanterre.fr>](mailto:lgrobol@parisnanterre.fr)


## HTML

Tutoriels interactifs sur [MDN Learn](https://developer.mozilla.org/en-US/docs/Learn) (ils sont
aussi disponibles en français)

- [*Getting started with
  HTML*](https://developer.mozilla.org/en-US/docs/Learn/HTML/Introduction_to_HTML/Getting_started)
- [*Web forms*](https://developer.mozilla.org/en-US/docs/Learn/Forms)
  - Il n'est pas forcément nécessaire de s'attarder trop longtemps sur les questions de style ou les
    contrôles avancé, l'objectif est d'arriver jusqu'à [*Sending and retrieving form
    data*](https://developer.mozilla.org/en-US/docs/Learn/Forms/Sending_and_retrieving_form_data)
- Ne pas hésiter à fouiller dans les autres parties du tutoriel (notamment CSS et JavaScript) pour
  mieux les comprendre. À faire selon vos goûts.

## 🥋 Exo 🥋

Concevoir

- Une page HTML avec un formulaire comprenant un champ de texte et un bouton de soumission.
  Assurez-vous qu'elle passe au [valideur du W3C](https://validator.w3.org)
- Une API avec FastAPI qui reçoit des requêtes de type POST venant de la page que vous avez créé et
  qui crée pour chacune un nouveau fichier texte sur votre machine dont le contenu est le contenu du
  champ de texte. **Vous aurez besoin de regarder [dans sa
  doc](https://fastapi.tiangolo.com/tutorial/request-forms/)** comment on récupère dans FastAPI des
  données envoyées depuis un formulaire (malheureusement ce n'est pas du JSON ! Pour ça il faut
  court-circuiter avec du JavaScript).
  - **Attention** les champs de formulaire sont référencés par leur attribut `name` dans une un
    envoi de formulaire via POST. Si cette phrase est complètement obscure pour vous, allez **lire
    les docs**.

## Générer du HTML en Python

**En général** quand on crée un service web, on a envie de lui donner une **interface web** lisible
par des humain⋅e⋅s. Autrement dit une page web.

C'est bien gentil de lire du JSON dans un navigateur, mais au bout d'un moment ça va bien.

On a vu comment récupérer des informations envoyées par l'utilisateur avec des formulaires,
maintenant on va voir comment lui répondre en affichant des données générées par notre programme.

Il va donc nous falloir *générer du HTML en Python*

### À la main

C'est-à-dire que HTML c'est du texte. Des chaînes de caractères donc.

Du coup vous pouvez en générer en Python, ça va, on sait faire.

In [ ]:
doc = """<!DOCTYPE html>
<html>
  <head>
    <meta charset="utf-8" />
    <title>What is the Average Flying Speed of an African Sparrow?</title>
  </head>
  <body>
    <h1>What is the Average Flying Speed of an African Sparrow?</h1>
    <p>The airspeed velocity of an unladen swallow is something like 20.1 miles per hour or 9 meters per second</p>
  </body>
</html>
"""
print(doc)

En plus dans un notebook ça se fait bien avec
[`IPython.display.HTML`](https://ipython.readthedocs.io/en/stable/api/generated/IPython.display.html#IPython.display.HTML)

In [ ]:
from IPython.display import HTML
HTML(doc)

Et vous savez comment écrire dans un fichier

In [ ]:
with open("local/spam.html", "w") as out_stream: 
    out_stream.write(doc)

Et voilà on a écrit [du HTML](local/spam.html).

### 🎈 Exo 🎈

Écrire une fonction qui prend en argument une liste de chaines de caractères et un chemin vers un
fichier et qui écrit dans ce fichier une page HTML qui contient une liste non-ordonnée dont les
éléments sont les chaînes passées en argument.

In [ ]:
def make_ul(elems: list[str], path: str):
    pass  # À vous de jouer

# Pour tester
make_ul(["The Beths", "Beirut", "Death Cab for Cutie"], "local/moody_bands.html")
with open("local/moody_bands.html") as in_stream:
    print(in_stream.read())

Bien entendu, vérifiez que votre HTML passe au [valideur du W3C](https://validator.w3.org).


### Avec `lxml`

lxml propose une interface sympa pour générer du HTML en étant sûr⋅e de ne pas faire d'erreurs de
syntaxe

In [ ]:
import lxml
from lxml.html import builder as E
html = E.HTML(
    E.HEAD(
        E.META(charset="utf-8"),
        E.TITLE("What is the Average Flying Speed of an African Sparrow?")
    ),
    E.BODY(
        E.H1("What is the Average Flying Speed of an African Sparrow?"),
        E.P("The airspeed velocity of an unladen swallow is something like 20.1 miles per hour or 9 meters per second"),
    )
)

print(lxml.html.tostring(html, encoding=str))

In [ ]:
HTML(lxml.html.tostring(html, encoding=str))

## Avec FastAPI

Pour afficher du HTML quand on accède à votre point d'accès FastAPI, vous pouvez utiliser
[`fastapi.responses.HTMLResponse`](https://fastapi.tiangolo.com/reference/responses/?h=html#fastapi.responses.HTMLResponse)
(qui n'est en fait rien de plus qu'un wrapper de
[`starlette.responses.HTMLResponses](https://www.starlette.io/responses/#htmlresponse)).
Fondamentalement, ça ne fait que mettre vos données dans une réponse générique avec un header
`media_type = "text/html"`, mais c'est plus lisible comme ça


In [ ]:
# %load examples/html_api.py
from fastapi import FastAPI
from fastapi.responses import HTMLResponse


app = FastAPI()


@app.get("/", response_class=HTMLResponse)
async def read_items():
    html_content = """
    <html>
        <head>
            <title>What is the Average Flying Speed of an African Sparrow?</title>
        </head>
        <body>
            <h1>What is the Average Flying Speed of an African Sparrow?</h1>
            <p>The airspeed velocity of an unladen swallow is something like 20.1 miles per hour or 9 meters per second</p>
        </body>
    </html>
    """
    return HTMLResponse(content=html_content, status_code=200)

Comme d'habitude, lancez depuis [`examples/`](examples/) avec 

```sh
uvicorn html_api:app
```

Et allez voir <http://localhost:8000>

## 🧊 Exo 🧊

1\. Concevoir une API qui reçoit des requêtes de type POST contenant une liste de chaînes de
caractère et répond avec une page HTML qui contient une liste ordonnée dont les éléments sont les
chaînes de caractères reçus.

Bien entendu, vérifiez que votre HTML passe au [valideur du W3C](https://validator.w3.org).


2\. Reprendre votre API précédente qui utilisait spaCy pour renvoyer les POS tag correspondant à
une requête et faites lui renvoyer une présentation des résultats en HTML plutôt que du JSON.


## Les templates avec Jinja

Vous avez dû vous en rendre compte, générer du HTML programmatiquement comme ça c'est plutôt pénible :

- En écrivant des chaînes de caractères à la main, c'est pas simple d'être dans les clous du valideur.
- Avec lxml, on doit manipuler des grosses hiérarchies d'objets compliqués, c'est vite le bazar.

En plus dans aucun des deux cas on a le confort de

- La coloration syntaxique du HTML
- Une gestion correcte par git
- …

Ce qui serait **bien** ça serait de pouvoir écrire du HTML normalement et en Python de ne faire que
changer les parties intéressantes.

Ça tombe bien, il y a des outils pour ça.

*Meet* [Jinja](https://jinja.palletsprojects.com).

### Jinja ?

Jinja.

Jinja est un « moteur de templates » (*template engine*), c'est un genre de `str.format` ou de
*f-string*. Voyez plutôt :

In [ ]:
from jinja2 import Template 
t = Template("Hello {{ something }}!")
t.render(something="World")

OK, super, mais ça on sait déjà faire

In [ ]:
s = "Hello {something}"
print(s.format(something="World"))

In [ ]:
something="World"
print(f"Hello {something}")

Du coup, qu'est-ce que ça apporte de plus ?

In [ ]:
t = Template("My favorite numbers: {% for n in numbers %} {{n}} {% endfor %}")
t.render(numbers=[2, 7, 1, 3])

C'est une boucle for !

À quoi ça sert ? Et bien par exemple on peut s'en servir pour générer des listes :

In [ ]:
t = Template("""Some interesting people:
<ul>
{% for p in people %}
<li>{{p.name}}, {{p.position}}</li>
{% endfor %}
</ul>
""")
lst = t.render(
    people=[
        {"name": "Guido van Rossum", "position": "Benevolent dictator for life"},
        {"name": "Ines Montani", "position": "Cofounder of explosion.ai"},
        {"name": "Kirby Conrod", "position": "Linguist and scholar"},
    ]
)

In [ ]:
print(lst)

In [ ]:
display(HTML(lst))

Petite subtilité : pour se débarrasser des lignes vides intempestives, [on peut utiliser un
`-`](https://jinja.palletsprojects.com/en/3.1.x/templates/#whitespace-control)

In [ ]:
t = Template("""Some interesting people:
<ul>
{% for p in people -%}
<li>{{p.name}}, {{p.position}}</li>
{% endfor -%}
</ul>
""")
lst = t.render(
    people=[
        {"name": "Guido van Rossum", "position": "Benevolent dictator for life"},
        {"name": "Ines Montani", "position": "Cofounder of explosion.ai"},
        {"name": "Kirby Conrod", "position": "Linguist and scholar"},
    ]
)
print(lst)

Il y a d'[autres](https://jinja.palletsprojects.com/en/3.1.x/templates/#list-of-control-structures)
fonctionnalités intéressantes dans les templates Jinja, comme les conditions et les macros. On ne va
pas rentrer dans le détail parce que c'est en général une meilleure idée de faire les traitements
compliqués côté Python, mais elles existent et peuvent être utiles à l'occasion.

Ce qui est plus intéressant pour nous, c'est la possibilité d'écrire nos templates dans des
fichiers. Voici par exemple le contenu de
[`examples/templates/basic.html.jinja`](examples/templates/basic.html.jinja) :

```django
<!DOCTYPE html>
<html lang="en">
<head>
    <title>My favourite people</title>
</head>
<body>
    <h1>My favourite people</h1>
    <ul>
        {% for p in people -%}
            <li>{{p.name}}, {{p.position}}</li>
        {% endfor -%}
    </ul>
</body>
</html>
```

On s'en sert ainsi

In [ ]:
from jinja2 import Environment, FileSystemLoader
env = Environment(
    loader=FileSystemLoader("examples/templates"),
)
t = env.get_template("basic.html.jinja")
lst = t.render(
    people=[
        {"name": "Guido van Rossum", "position": "Benevolent dictator for life"},
        {"name": "Ines Montani", "position": "Cofounder of explosion.ai"},
        {"name": "Kirby Conrod", "position": "Linguist and scholar"},
    ]
)
print(lst)

Ça permet de séparer un peu plus la partie **traitement des données** qui est gérée par cotre code
Python et la partie **affichage** des données qui est gérée en Jinja.

En plus, les bons IDE supportent la syntaxe de Jinja, vous devriez donc au moins avoir de la coloration syntaxique !

Parmi les autres fonctions intéressantes, Jinja permet d'échapper automatiquement le HTML, afin de
se prémunir des injections de code. Par exemple si on reprend l'environnement précédent, mais qu'on
change un peu les données (ce qui peut arriver si les données en question ne sont pas gérées
directement par vous, mais sont issues des utilisateurices de votre application).

In [ ]:
lst = t.render(
    people=[
        {"name": "<strong>Guido</strong> van Rossum", "position": "Benevolent dictator for life"},
        {"name": "Ines Montani", "position": "cofounder of explosion.ai"},
        {"name": "Kirby Conrod", "position": "Linguist and scholar"},
    ]
)
print(lst)
display(HTML(lst))

Évidemment ici ce n'est pas très grave, `<strong>` n'est pas un tag très dangereux. En revanche on
peut faire beaucoup de choses avec `<script>`. Pour un exemple, décommentez la dernière ligne de la
cellule suivante, puis exécutez-la.

In [ ]:
lst = t.render(
    people=[
        {"name": "<script>alert('boo!')</script>Guido van Rossum", "position": "Benevolent dictator for life"},
        {"name": "Ines Montani", "position": "cofounder of explosion.ai"},
        {"name": "Kirby Conrod", "position": "Linguist and scholar"},
    ]
)
print(lst)
# display(HTML(lst)) 

Pour éviter ça :


In [ ]:
env = Environment(
    loader=FileSystemLoader("examples/templates"),
    autoescape=True,
)

t = env.get_template("basic.html.jinja")
lst = t.render(
    people=[
        {"name": "<script>alert('boo!')</script>Guido van Rossum", "position": "Benevolent dictator for life"},
        {"name": "Ines Montani", "position": "cofounder of explosion.ai"},
        {"name": "Kirby Conrod", "position": "Linguist and scholar"},
    ] 
)
print(lst)
display(HTML(lst)) 

## FastAPI et Jinja

Les deux s'interfacent bien, ou plus précisément, FastAPI propose des interfaces vers Jinja

Voici le contenu de [`examples/templates/hello.html.jinja`](examples/templates/jinja_api.py)

```django
<!DOCTYPE html>
<html lang="en">
<head>
    <title>Hello, {{name}}</title>
</head>
<body>
    <h1>Hello, {{name}}</h1>
    <p>How do you do, fellow kids?</p>
</body>
</html>
```

Et de [`examples/jinja_api.py`](examples/jinja_api.py)

In [ ]:
# %load examples/jinja_api.py
from fastapi import FastAPI, Request
from fastapi.responses import HTMLResponse
from fastapi.templating import Jinja2Templates

app = FastAPI()

templates = Jinja2Templates(directory="templates")


# Le paramètre `request` est obligatoire, c'est la faute à Starlette !
@app.get("/hello/{name}", response_class=HTMLResponse)
async def read_item(request: Request, name: str):
    return templates.TemplateResponse(
        "hello.html.jinja", {"request": request, "name": name}
    )


Lancez cette API avec `uvicorn jinja_api:app` et allez à <http://localhost:8000/hello/world>


## 🙄 Exo 🙄

Reprenez les APIs de 🧊 et réécrivez-les en Jinja. C'est pour votre bien.